In [78]:
#Plot
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

#Data Packages
import math
import pandas
import numpy as np
import pandas as pd
#Progress bar
from tqdm import tqdm

#Counter
from collections import Counter

#Operation
import operator

#Natural Language Processing Packages
import re
import nltk
import string

## Download Resources
nltk.download("vader_lexicon")
nltk.download("stopwords")
nltk.download("averaged_perceptron_tagger")
nltk.download("wordnet")

from nltk.sentiment import SentimentAnalyzer
from nltk.sentiment.vader import SentimentIntensityAnalyzer
from nltk.sentiment.util import *
from nltk import tokenize
from nltk.corpus import stopwords
from nltk.tag import PerceptronTagger
from nltk.data import find

## Machine Learning
import sklearn
import sklearn.metrics as metrics

[nltk_data] Downloading package vader_lexicon to
[nltk_data]     C:\Users\Litos\AppData\Roaming\nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Litos\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\Litos\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Litos\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [2]:
# Use vader to evaluated sentiment of reviews (vader score for each entire review)
def evalSentences(sentences, to_df=False, columns=[]):
    #Instantiate an instance to access SentimentIntensityAnalyzer class
    sid = SentimentIntensityAnalyzer()
    pdlist = []
    if to_df:
        for sentence in tqdm(sentences):
            ss = sid.polarity_scores(sentence)
            pdlist.append([sentence]+[ss['compound']])
        reviewDf = pandas.DataFrame(pdlist)
        reviewDf.columns = columns
        return reviewDf
    
    else:
        for sentence in tqdm(sentences):
            print(sentence)
            ss = sid.polarity_scores(sentence)
            for k in sorted(ss):
                print('{0}: {1}, '.format(k, ss[k]), end='')
            print()

In [163]:
sentence = 'quick service'
sid = SentimentIntensityAnalyzer()
ss = sid.polarity_scores(sentence)
ss

{'compound': 0.0, 'neg': 0.0, 'neu': 1.0, 'pos': 0.0}

# Load Data

In [3]:
cur_df = pd.read_csv('../../data/yelp/Data.csv', index_col=0,  encoding='latin-1')

In [6]:
reviews = cur_df['review_text'].values

In [7]:
reviewDF = evalSentences(reviews, to_df=True, columns=['reviewCol','vader'])

100%|█████████████████████████████████████████████████████████████████████████| 169961/169961 [05:04<00:00, 557.57it/s]


In [30]:
cur_df['Binary_vader'] = (reviewDF['vader']> 0.05)*[1]

In [9]:
# #Save
# reviewDF.to_csv('../../data/yelp/reviewDF.csv')

In [4]:
# Load reviewDF
reviewDF = pd.read_csv('../../data/yelp/reviewDF.csv', index_col=0,  encoding='latin-1')

In [5]:
reviewDF.head()

reviewCol   vader
0  I ordered the lemon mango slush and the lemon ...  0.9758
1  Came here on a Sunday afternoon, it wasn't bus...  0.9763
2  {Grapefruit & Yakult Green Tea with Aloe Jelly...  0.9170
3  Saw this newly opened bubble tea shop and want...  0.9898
4  Happy Lemon has become my new favourite place ...  0.9922

In [5]:
cur_df['vader'] = reviewDF['vader']

# Find most sentiment words by Mutual Information

## Data preprocessing

In [6]:
# Note: You may want to use an NLTK tokenizer instead of a regular expression in the following
def dataFrameTransformation(hotelDf, reviewDF, k=500):
    reviews = reviewDF['reviewCol'].values
    
    stop = set(stopwords.words('english'))
    # Lowercase
    reviews = [w.lower() for w in reviews]
    
    # Top-k frequent terms
    counter = Counter()
    for review in tqdm(reviews):
            counter.update([word.lower() 
                            for word 
                            in re.findall(r'\w+', review) 
                            if word.lower() not in stop and len(word) > 2])
    topk = counter.most_common(k)        
    
    #Find out if a particular review has the word from topk list
    freqReview = []
    for i in tqdm(range(len(reviews))):
        tempCounter = Counter([word.lower() for word in re.findall(r'\w+',reviews[i])])
        topkinReview = [1 if tempCounter[word] > 0 else 0 for (word,wordCount) in topk]
        freqReview.append(topkinReview)
        
        
    #Prepare freqReviewDf
    freqReviewDf = pandas.DataFrame(freqReview)
    dfName = []
    for c in topk:
        dfName.append(c[0])
    freqReviewDf.columns = dfName
    finalreviewDf = reviewDF.join(freqReviewDf)
    finaldf = hotelDf.join(finalreviewDf)
    return topk, finaldf

In [7]:
text = nltk.word_tokenize(reviewDF['reviewCol'][0])

In [8]:
from nltk.stem import WordNetLemmatizer
def preprocess(text):
#     text = text.replace('.',' ').replace('/',' ').replace('quot;', ' ').replace('amp;', '').replace('-', ' ')
    
    text = text.replace('.',' ').replace('/t',' ').replace('\t',' ').replace('/',' ').replace('-',' ')
    
    # Tokenize
    text = nltk.word_tokenize(text)
    
    # Lowercase
    text = [w.lower() for w in text]

    # Remove Punctuation
    table = str.maketrans('', '', string.punctuation)
    text = [w.translate(table) for w in text]

    # Remove tokens that are not alphabetic
    text = [w for w in text if w.isalpha()]

    # Remove Stopwords
    # Get english stopwords
    en_stopwords = set(stopwords.words('english'))
    en_stopwords.remove('off')
    text = [w for w in text if w not in en_stopwords]
    
    # Lemmatizing
    lemmatizer = WordNetLemmatizer()
    text = [lemmatizer.lemmatize(w) for w in text]

    text = " " + " ".join(str(x) for x in text) + " "

    text = text.replace('whitish', 'white')
    text = text.replace('bisquity', ' biscuit ')
    text = text.replace('carmel', ' caramel ')
    text = text.replace('flower', ' floral ')
    text = text.replace('piny', ' pine ')
    text = text.replace('off white', 'offwhite')
    text = text.replace('goden', 'gold')
    text = text.replace('yello', 'yellow')
    text = text.replace('reddish', ' red ') 
    text = text.replace('favorite', 'favourite ') 
    

    # Reset to token
    text = nltk.word_tokenize(text)
    table = str.maketrans('', '', string.punctuation)
    text = [w.translate(table) for w in text]
    text = [w for w in text if w.isalpha()]
#     en_stopwords = set(stopwords.words('english'))
    text = [w for w in text if w not in en_stopwords]
    lemmatizer = WordNetLemmatizer()
    text = [lemmatizer.lemmatize(w) for w in text]
    
    return text

# Compute Mutual Info

In [9]:
# get Top K mutual information terms from the dataframe
def getMI(topk, df, label_column='groundTruth'):
    miScore = []
    for word in topk:
        miScore.append([word[0]]+[metrics.mutual_info_score(finaldf[label_column], finaldf[word[0]])])
    miScoredf = pandas.DataFrame(miScore).sort_values(1,ascending=0)
    miScoredf.columns = ['Word','MI Score']
    return miScoredf

# Noun Phrase

In [10]:
# Sample text
text = """The Buddha, the Godhead, resides quite as comfortably in the circuits of a digital
computer or the gears of a cycle transmission as he does at the top of a mountain
or in the petals of a flower. To think otherwise is to demean the Buddha...which is
to demean oneself."""

In [11]:
tagger = PerceptronTagger()
# Part of Speech Tagging
# Google: https://en.wikipedia.org/wiki/Part-of-speech_tagging
pos_tag = tagger.tag
taggedToks = pos_tag(re.findall(r'\w+', text))
taggedToks

[('The', 'DT'),
 ('Buddha', 'NNP'),
 ('the', 'DT'),
 ('Godhead', 'NNP'),
 ('resides', 'VBZ'),
 ('quite', 'RB'),
 ('as', 'IN'),
 ('comfortably', 'RB'),
 ('in', 'IN'),
 ('the', 'DT'),
 ('circuits', 'NNS'),
 ('of', 'IN'),
 ('a', 'DT'),
 ('digital', 'JJ'),
 ('computer', 'NN'),
 ('or', 'CC'),
 ('the', 'DT'),
 ('gears', 'NNS'),
 ('of', 'IN'),
 ('a', 'DT'),
 ('cycle', 'NN'),
 ('transmission', 'NN'),
 ('as', 'IN'),
 ('he', 'PRP'),
 ('does', 'VBZ'),
 ('at', 'IN'),
 ('the', 'DT'),
 ('top', 'NN'),
 ('of', 'IN'),
 ('a', 'DT'),
 ('mountain', 'NN'),
 ('or', 'CC'),
 ('in', 'IN'),
 ('the', 'DT'),
 ('petals', 'NNS'),
 ('of', 'IN'),
 ('a', 'DT'),
 ('flower', 'NN'),
 ('To', 'TO'),
 ('think', 'VB'),
 ('otherwise', 'RB'),
 ('is', 'VBZ'),
 ('to', 'TO'),
 ('demean', 'VB'),
 ('the', 'DT'),
 ('Buddha', 'NNP'),
 ('which', 'WDT'),
 ('is', 'VBZ'),
 ('to', 'TO'),
 ('demean', 'VB'),
 ('oneself', 'PRP')]

In [12]:
text = cur_df['conca_review'][0]

In [13]:
tagger = PerceptronTagger()
# Part of Speech Tagging
# Google: https://en.wikipedia.org/wiki/Part-of-speech_tagging
pos_tag = tagger.tag
taggedToks = pos_tag(re.findall(r'\w+', text))
taggedToks

[('ordered', 'JJ'),
 ('lemon', 'NN'),
 ('mango', 'NN'),
 ('slush', 'NN'),
 ('lemon', 'NN'),
 ('taste', 'NN'),
 ('strong', 'JJ'),
 ('love', 'NN'),
 ('lemon', 'NN'),
 ('love', 'NN'),
 ('drink', 'NN'),
 ('informed', 'VBN'),
 ('jelly', 'RB'),
 ('drink', 'VB'),
 ('added', 'VBD'),
 ('bonus', 'NN'),
 ('since', 'IN'),
 ('love', 'NN'),
 ('drink', 'NN'),
 ('topping', 'VBG'),
 ('jelly', 'RB'),
 ('different', 'JJ'),
 ('compared', 'VBN'),
 ('bubble', 'JJ'),
 ('tea', 'JJ'),
 ('place', 'NN'),
 ('soft', 'JJ'),
 ('chewy', 'NN'),
 ('overall', 'JJ'),
 ('enjoyed', 'VBD'),
 ('drink', 'NN')]

In [14]:
# This grammar is described in the paper by S. N. Kim,
# T. Baldwin, and M.-Y. Kan.
# Evaluating n-gram based evaluation metrics for automatic
# keyphrase extraction.
# Technical report, University of Melbourne, Melbourne 2010.
grammar = r"""
    NBAR:
        {<NN.*|JJ>*<NN.*>}  # Nouns and Adjectives, terminated with Nouns
        
    NP:
        {<NBAR>}
        {<NBAR><IN><NBAR>}  # Above, connected with in/of/etc...
"""

In [15]:
# Create phrase tree
chunker = nltk.RegexpParser(grammar)
tree= chunker.parse(taggedToks)

In [16]:
# Noun Phrase Extraction Support Functions
from nltk.corpus import stopwords
stopwords = stopwords.words('english')
lemmatizer = nltk.WordNetLemmatizer()
stemmer = nltk.stem.porter.PorterStemmer()

# generator, generate leaves one by one
def leaves(tree):
    """Finds NP (nounphrase) leaf nodes of a chunk tree."""
    for subtree in tree.subtrees(filter = lambda t: t.label()=='NP' or t.label()=='JJ' or t.label()=='RB'):
        yield subtree.leaves()

# stemming, lematizing, lower case... 
def normalise(word):
    """Normalises words to lowercase and stems and lemmatizes it."""
    word = word.lower()
    word = stemmer.stem(word)
    word = lemmatizer.lemmatize(word)
    return word

# stop-words and length control
def acceptable_word(word):
    """Checks conditions for acceptable word: length, stopword."""
    accepted = bool(2 <= len(word) <= 40
        and word.lower() not in stopwords)
    return accepted

# generator, create item once a time
def get_terms(tree):
    for leaf in leaves(tree):
#         term = [normalise(w) for w,t in leaf if acceptable_word(w) ]
        term = [w for w,t in leaf if acceptable_word(w) ] # without normalise
        # Phrase only
        if len(term)>1:
            yield term

In [17]:
stemmer.stem('chewy')

'chewi'

In [18]:
# Traverse tree and get noun phrases
npTokenList = [word for word in get_terms(tree)]

npTokenList

[['ordered',
  'lemon',
  'mango',
  'slush',
  'lemon',
  'taste',
  'strong',
  'love',
  'lemon',
  'love',
  'drink'],
 ['love', 'drink'],
 ['bubble', 'tea', 'place', 'soft', 'chewy']]

In [19]:
# Flatten phrase lists to get tokens for analysis
def flatten(npTokenList):
    finalList =[]
    for phrase in npTokenList:
        token = ''
        for word in phrase:
            token += word + ' '
#         finalList.append(token.rstrip())
        finalList.append(token)
    return finalList

In [20]:
finalList = flatten(npTokenList)

In [21]:
finalList

['ordered lemon mango slush lemon taste strong love lemon love drink ',
 'love drink ',
 'bubble tea place soft chewy ']

In [22]:
review = cur_df["conca_review"].values[0]
pos_tag(re.findall(r'\w+', review))

[('ordered', 'JJ'),
 ('lemon', 'NN'),
 ('mango', 'NN'),
 ('slush', 'NN'),
 ('lemon', 'NN'),
 ('taste', 'NN'),
 ('strong', 'JJ'),
 ('love', 'NN'),
 ('lemon', 'NN'),
 ('love', 'NN'),
 ('drink', 'NN'),
 ('informed', 'VBN'),
 ('jelly', 'RB'),
 ('drink', 'VB'),
 ('added', 'VBD'),
 ('bonus', 'NN'),
 ('since', 'IN'),
 ('love', 'NN'),
 ('drink', 'NN'),
 ('topping', 'VBG'),
 ('jelly', 'RB'),
 ('different', 'JJ'),
 ('compared', 'VBN'),
 ('bubble', 'JJ'),
 ('tea', 'JJ'),
 ('place', 'NN'),
 ('soft', 'JJ'),
 ('chewy', 'NN'),
 ('overall', 'JJ'),
 ('enjoyed', 'VBD'),
 ('drink', 'NN')]

In [23]:
flatten([word for word in get_terms(chunker.parse(pos_tag(re.findall(r'\w+', review))))])


['ordered lemon mango slush lemon taste strong love lemon love drink ',
 'love drink ',
 'bubble tea place soft chewy ']

In [24]:
cur_df['review'][1]

"['came', 'sunday', 'afternoon', 'nt', 'busy', 'came', 'sunday', 'special', 'medium', 'bubble', 'milk', 'tea', 'cream', 'puff', 'friend', 'hand', 'ordered', 'oreo', 'milk', 'tea', 'medium', 'size', 'medium', 'cup', 'little', 'bigger', 'small', 'size', 'bubble', 'tea', 'location', 'much', 'smaller', 'medium', 'please', 'see', 'picture', 'bubble', 'milk', 'tea', 'cream', 'puff', 'typical', 'normal', 'nothing', 'special', 'bubble', 'nt', 'taste', 'great', 'oreo', 'milk', 'certainly', 'different', 'milk', 'tea', 'crushed', 'oreo', 'friend', 'liked', 'thought', 'kind', 'weird', 'texture', 'oreo', 'grainy', 'definitely', 'different', 'think', 'place', 'bit', 'priced', 'regular', 'medium', 'drink', 'cost', 'minimum', 'definitely', 'place', 'make', 'bubble', 'taste', 'better', 'since', 'pmall', 'lot', 'different', 'bubble', 'tea', 'place', 'may', 'coming', 'back', 'unless', 'good', 'deal', 'fancy', 'flavour']"

In [25]:
review

' ordered lemon mango slush lemon taste strong love lemon love drink informed jelly drink added bonus since love drink topping jelly different compared bubble tea place soft chewy overall enjoyed drink '

In [76]:
from ast import literal_eval

# Revise the previous dataframe transform function...
def newDataFrameTransformation(hotelDf, reviewDF, reviewcol_name = 'conca_review',k= 1000):
#     reviews = reviewDF[reviewcol_name].values
    reviews = hotelDf[reviewcol_name].values
    
    # Top-k frequent terms
    counter = Counter()
    for review in tqdm(reviews):
        counter.update(flatten([word
                            for word 
                            in get_terms(chunker.parse(pos_tag(re.findall(r'\w+', review)))) 
                            ]))
    topk = counter.most_common(k)        
    
    #Find out if a particular review has the word from topk list
    freqReview = []
    for i in tqdm(range(len(reviews))):
        tempCounter = Counter(flatten([word 
                                       for word 
                                       in get_terms(chunker.parse(pos_tag(re.findall(r'\w+',reviews[i]))))]))
        topkinReview = [1 if tempCounter[word] > 0 else 0 for (word,wordCount) in topk]
        freqReview.append(topkinReview)
         
    #Prepare freqReviewDf
    freqReviewDf = pandas.DataFrame(freqReview)
    dfName = []
    for c in topk:
        dfName.append(c[0])
    freqReviewDf.columns = dfName
    finalreviewDf = reviewDF.join(freqReviewDf)
    finaldf = hotelDf[['business_id','rating','Binary','review','conca_review','UserIndex','ItemIndex']].join(finalreviewDf)
    return topk, finaldf

def preprocess(text):

    text = text.replace('.',' ').replace('/t',' ').replace('\t',' ').replace('/',' ').replace('-',' ')
    
    # Tokenize
    text = nltk.word_tokenize(text)
    
    # Lowercase
    text = [w.lower() for w in text]

    # Remove Punctuation
    table = str.maketrans('', '', string.punctuation)
    text = [w.translate(table) for w in text]

    # Remove tokens that are not alphabetic
    text = [w for w in text if w.isalpha()]

    # Remove Stopwords
    # Get english stopwords
    en_stopwords = set(stopwords.words('english'))
    en_stopwords.remove('off')
    text = [w for w in text if w not in en_stopwords]
    
    # Lemmatizing
    lemmatizer = WordNetLemmatizer()
    text = [lemmatizer.lemmatize(w) for w in text]

    text = " " + " ".join(str(x) for x in text) + " "

    text = text.replace('whitish', 'white')
    text = text.replace('bisquity', ' biscuit ')
    text = text.replace('carmel', ' caramel ')
    text = text.replace('flower', ' floral ')
    text = text.replace('piny', ' pine ')
    text = text.replace('off white', 'offwhite')
    text = text.replace('goden', 'gold')
    text = text.replace('yello', 'yellow')
    text = text.replace('reddish', ' red ') 
    text = text.replace('favorite', 'favourite ') 
    

    # Reset to token
    text = nltk.word_tokenize(text)
    table = str.maketrans('', '', string.punctuation)
    text = [w.translate(table) for w in text]
    text = [w for w in text if w.isalpha()]
#     en_stopwords = set(stopwords.words('english'))
    text = [w for w in text if w not in en_stopwords]
    lemmatizer = WordNetLemmatizer()
    text = [lemmatizer.lemmatize(w) for w in text]
    
    return text

def preprocess_sentence(sentence):
    return ' '.join(str(x) for x in preprocess(sentence))

In [28]:
topk_phrase, finaldf_phrase = newDataFrameTransformation(cur_df, reviewDF, k = 2000)


  1%|▌                                                                          | 1213/169961 [00:07<13:57, 201.44it/s]


  2%|█▏                                                                         | 2611/169961 [00:15<17:45, 157.02it/s]


  2%|█▋                                                                         | 3932/169961 [00:22<15:04, 183.50it/s]


  3%|██▎                                                                        | 5236/169961 [00:30<15:41, 175.02it/s]


  4%|██▉                                                                        | 6578/169961 [00:38<15:32, 175.29it/s]


...

 98%|███████████████████████████████████████████████████████████████████████▎ | 165905/169961 [18:25<00:25, 156.21it/s]


 98%|███████████████████████████████████████████████████████████████████████▊ | 167117/169961 [18:33<00:18, 154.48it/s]


 99%|████████████████████████████████████████████████████████████████████████▎| 168272/169961 [18:41<00:11, 144.85it/s]


100%|████████████████████████████████████████████████████████████████████████▊| 169400/169961 [18:48<00:03, 140.98it/s]


100%|█████████████████████████████████████████████████████████████████████████| 169961/169961 [18:52<00:00, 150.08it/s]


topk_phrase

In [29]:
# Compute PMI for all terms and all possible labels
def pmiForAllCal(df, label_column='Binary', topk=topk_phrase):
    #Try calculate all the pmi for top k and store them into one pmidf dataframe
    pmilist = []
    pmiposlist = []
    pmineglist = []
    for word in tqdm(topk):
#         pmilist.append([word[0]]+[pmiCal(df,word[0])])
        pmiposlist.append([word[0]]+[pmiIndivCal(df,word[0],1,label_column)])
        pmineglist.append([word[0]]+[pmiIndivCal(df,word[0],0,label_column)])
    pmidf = pandas.DataFrame(pmilist)
    pmiposlist = pandas.DataFrame(pmiposlist)
    pmineglist = pandas.DataFrame(pmineglist)
    pmiposlist.columns = ['word','pmi']
    pmineglist.columns = ['word','pmi']
#     pmidf.columns = ['word','pmi']
#     return pmiposlist, pmineglist, pmidf
    return pmiposlist, pmineglist

def pmiIndivCal(df,x,gt, label_column='Binary'):
    px = sum(df[label_column]==gt)/len(df)
    py = sum(df[x]==1)/len(df)
    pxy = len(df[(df[label_column]==gt) & (df[x]==1)])/len(df)
    if pxy==0:#Log 0 cannot happen
        pmi = math.log((pxy+0.0001)/(px*py))
    else:
        pmi = math.log(pxy/(px*py))
    return pmi

# Simple example of getting pairwise mutual information of a term
def pmiCal(df, x):
    pmilist=[]
    for i in [1,0]:
        for j in [0,1]:
            px = sum(df['Binary']==i)/len(df)
            py = sum(df[x]==j)/len(df)
            pxy = len(df[(df['Binary']==i) & (df[x]==j)])/len(df)
            if pxy==0:#Log 0 cannot happen
                pmi = math.log((pxy+0.0001)/(px*py))
            else:
                pmi = math.log(pxy/(px*py))
            pmilist.append([i]+[j]+[px]+[py]+[pxy]+[pmi])
    pmidf = pandas.DataFrame(pmilist)
    pmidf.columns = ['x','y','px','py','pxy','pmi']
    return pmidf

In [112]:
pmiposlist, pmineglist = pmiForAllCal(finaldf_phrase, topk=topk_phrase)

NameError: name 'pmiForAllCal' is not defined

In [ ]:
pmiposlist_vader, pmineglist_vader = pmiForAllCal(finaldf_phrase, topk=topk_phrase,label_column='vader')

In [62]:
import pickle as pkl
with open("pmineglist", "wb") as output_file:
    pkl.dump(pmineglist, output_file)
with open("pmiposlist", "wb") as output_file:
    pkl.dump(pmiposlist, output_file)

In [69]:
# topk_phrase, finaldf_phrase
with open("finaldf_phrase", "wb") as output_file:
    pkl.dump(finaldf_phrase, output_file)


## Keyphrase for positive and negative rating

In [87]:
neg_rating = pmineglist.sort_values('pmi',ascending=0)
neg_rating = neg_rating['word'][:50].tolist()

In [91]:
neg_rating

['bad place',
 'okay noth',
 'decent place',
 'ok noth',
 'decent food',
 'second chanc',
 'terribl servic',
 'mediocr food',
 'decent servic',
 'eye contact',
 'sub par',
 'slow servic',
 'high hope',
 'dri side',
 'bit bland',
 'separ bill',
 'high price',
 'empti tabl',
 'poor servic',
 'room temperatur',
 'littl bland',
 'good dish',
 'bad tast',
 'averag price',
 'asian legend',
 'quick meal',
 'good overal',
 'bad servic',
 'salti side',
 'high side',
 'swiss chalet',
 'non exist',
 'plu side',
 'extra star',
 'wow factor',
 'long wait time',
 'bad day',
 'dim sum place',
 'bit pricey',
 'instant noodl',
 'chicken piec',
 'good locat',
 'small portion',
 'beef noodl',
 'good place',
 'much sauc',
 'decent portion',
 'good noth',
 'deer garden',
 'la carnita']

In [88]:
print ('[%s]' % ', '.join(map(str, neg_rating)))

[bad place, okay noth, decent place, ok noth, decent food, second chanc, terribl servic, mediocr food, decent servic, eye contact, sub par, slow servic, high hope, dri side, bit bland, separ bill, high price, empti tabl, poor servic, room temperatur, littl bland, good dish, bad tast, averag price, asian legend, quick meal, good overal, bad servic, salti side, high side, swiss chalet, non exist, plu side, extra star, wow factor, long wait time, bad day, dim sum place, bit pricey, instant noodl, chicken piec, good locat, small portion, beef noodl, good place, much sauc, decent portion, good noth, deer garden, la carnita]


In [89]:
pos_rating = pmiposlist.sort_values('pmi',ascending=0)
pos_rating = pos_rating['word'][:50].tolist()

In [90]:
print ('[%s]' % ', '.join(map(str, pos_rating)))

[amaz experi, favourit restaur, amaz servic, wonder experi, amaz food, great recommend, favorit place, hidden gem, hair cut, perfect balanc, favourit place, littl gem, much fun, favourit spot, escap room, super help, great coffe, real deal, great custom servic, person favourit, great qualiti, top notch, tast menu, delici food, great job, super nice, awesom place, great experi, delici meal, excel servic, perfect amount, singl time, mani flavour, great staff, nail salon, farmer market, bang bang, sure everyth, perfect place, sushi bar, favourit thing, great servic, vietnames coffe, special occas, great price, good reason, foie gra, friendli staff, board game, filet mignon]


In [92]:
pos_rating

['amaz experi',
 'favourit restaur',
 'amaz servic',
 'wonder experi',
 'amaz food',
 'great recommend',
 'favorit place',
 'hidden gem',
 'hair cut',
 'perfect balanc',
 'favourit place',
 'littl gem',
 'much fun',
 'favourit spot',
 'escap room',
 'super help',
 'great coffe',
 'real deal',
 'great custom servic',
 'person favourit',
 'great qualiti',
 'top notch',
 'tast menu',
 'delici food',
 'great job',
 'super nice',
 'awesom place',
 'great experi',
 'delici meal',
 'excel servic',
 'perfect amount',
 'singl time',
 'mani flavour',
 'great staff',
 'nail salon',
 'farmer market',
 'bang bang',
 'sure everyth',
 'perfect place',
 'sushi bar',
 'favourit thing',
 'great servic',
 'vietnames coffe',
 'special occas',
 'great price',
 'good reason',
 'foie gra',
 'friendli staff',
 'board game',
 'filet mignon']

# Vader 

In [32]:
# Get vader binary values
finaldf_phrase['Binary_vader'] = (finaldf_phrase['vader'] > 0.05)*[1]

pmiposlist_vader, pmineglist_vader = pmiForAllCal(finaldf_phrase, topk=topk_phrase,label_column='Binary_vader')

In [103]:
pos_rating = pmiposlist_vader.sort_values('pmi',ascending=0)
pos_rating = pos_rating['word'][:50].tolist()

In [104]:
pos_rating

['nice experi',
 'dim light',
 'great atmospher',
 'good care',
 'special event',
 'nice balanc',
 'super nice',
 'nice crunch',
 'great recommend',
 'perfect size',
 'nice chang',
 'great addit',
 'perfect amount',
 'perfect balanc',
 'gener amount',
 'interior design',
 'super tender',
 'great spot',
 'great textur',
 'great job',
 'great option',
 'amaz food',
 'good vibe',
 'welcom addit',
 'sweet tooth',
 'littl gem',
 'nice surpris',
 'winterlici menu',
 'nice textur',
 'great vibe',
 'great choic',
 'super help',
 'littl salti',
 'delici servic',
 'perfect spot',
 'great coffe',
 'larg window',
 'nice kick',
 'favourit part',
 'grill octopu',
 'special occas',
 'brussel sprout',
 'good friend',
 'nice place',
 'duck confit',
 'much fun',
 'great way',
 'summer time',
 'pleasant surpris',
 'good balanc']

In [106]:
neg_rating = pmineglist_vader.sort_values('pmi',ascending=0)
neg_rating = neg_rating['word'][:50].tolist()

In [107]:
print ('[%s]' % ', '.join(map(str, pos_rating)))

[nice experi, dim light, great atmospher, good care, special event, nice balanc, super nice, nice crunch, great recommend, perfect size, nice chang, great addit, perfect amount, perfect balanc, gener amount, interior design, super tender, great spot, great textur, great job, great option, amaz food, good vibe, welcom addit, sweet tooth, littl gem, nice surpris, winterlici menu, nice textur, great vibe, great choic, super help, littl salti, delici servic, perfect spot, great coffe, larg window, nice kick, favourit part, grill octopu, special occas, brussel sprout, good friend, nice place, duck confit, much fun, great way, summer time, pleasant surpris, good balanc]


In [108]:
print ('[%s]' % ', '.join(map(str, neg_rating)))

[terribl servic, poor servic, bad tast, bad servic, eye contact, bad day, mediocr food, bad review, bad experi, empti tabl, sub par, canadian tire, tini piec, food order, half way, custom servic, stinki tofu, neg review, instant noodl, room temperatur, cash regist, full price, first place, entir restaur, multipl time, ten minut, numer time, nail salon, last time, half hour, dim light, high price, drink order, high hope, everi time, pita bread, front desk, great recommend, nice balanc, special event, entir time, whole time, phone number, last visit, small piec, asian legend, kitchen staff, hair cut, posit review, star review]


# Updated Vader Keyphrases

In [115]:
pmiposlist, pmineglist = pmiForAllCal(finaldf_phrase, topk=topk_phrase)

  1%|▉                                                                               | 11/1000 [00:09<13:20,  1.24it/s]

KeyboardInterrupt: 

In [33]:
pmiposlist_vader, pmineglist_vader = pmiForAllCal(finaldf_phrase, topk=topk_phrase,label_column='Binary_vader')


  3%|██▋                                                                             | 67/2000 [00:53<23:53,  1.35it/s]


  7%|█████▎                                                                         | 135/2000 [01:44<23:00,  1.35it/s]


 10%|████████                                                                       | 203/2000 [02:34<22:11,  1.35it/s]


 14%|██████████▋                                                                    | 271/2000 [03:24<21:02,  1.37it/s]


 17%|█████████████▍                                                                 | 339/2000 [04:14<20:16,  1.37it/s]


...

 88%|████████████████████████████████████████████████████████████████████▉         | 1767/2000 [21:54<02:49,  1.38it/s]


 92%|███████████████████████████████████████████████████████████████████████▌      | 1835/2000 [22:45<02:00,  1.37it/s]


 95%|██████████████████████████████████████████████████████████████████████████▏   | 1903/2000 [23:34<01:11,  1.36it/s]


 99%|████████████████████████████████████████████████████████████████████████████▊ | 1971/2000 [24:24<00:22,  1.28it/s]


100%|██████████████████████████████████████████████████████████████████████████████| 2000/2000 [24:46<00:00,  1.35it/s]


In [34]:
neg_rating = pmineglist_vader.sort_values('pmi',ascending=0)
neg_rating = neg_rating['word'][:50].tolist()

# Some engineering work (mannually pick some word) 

In [148]:
pos_rating = pmiposlist_vader.sort_values('pmi',ascending=0)
pos_rating = pos_rating.reset_index()
# pos_rating = pos_rating['word'][:50].tolist()

In [149]:
neg_rating = pmineglist_vader.sort_values('pmi',ascending=0)
neg_rating = neg_rating.reset_index()
# neg_rating = neg_rating['word'][:50].tolist()

In [148]:
temp = np.where(neg_rating['word'].str.contains('good'))
neg_rating.loc[temp]

TypeError: list indices must be integers or slices, not str

In [151]:
temp1 = np.where(pos_rating['word'].str.contains('fast'))
pos_rating.loc[temp1]

index                 word       pmi
359    487        fast service   0.038786
394    911  breakfast sandwich   0.035335
584    889     breakfast place   0.015132

In [197]:
temp1 = np.where(pos_rating['word'].str.contains('atmosphere'))
pos_rating.loc[temp1]

Empty DataFrame
Columns: [index, word, pmi]
Index: []

In [150]:
# First find the reviews that contains the word 
key_word = 'comfortable'
target_df = cur_df['review_text'].loc[np.where(cur_df['review_text'].str.contains(key_word))]
target_df_index = np.where(cur_df['review_text'].str.contains(key_word))[0]
cur_df.loc[target_df_index]

Unnamed: 0.1  Unnamed: 0.1.1             business_id  friend_count  \
147              637             637  gISrxk4A5dfrjDivkC-L-Q            50   
164              693             693  gISrxk4A5dfrjDivkC-L-Q            53   
190              773             773  5C57zUQdzvNrCus8JBawmQ           120   
312             1578            1578  PxH02Eu2Z4MUycBLU80D8g           175   
313             1608            1608  PxH02Eu2Z4MUycBLU80D8g             1   
318             1634            1634  PxH02Eu2Z4MUycBLU80D8g           145   
487             2455            2455  1cGgVvEbuBlW2GDvJ112vA            64   
492             2462            2462  1cGgVvEbuBlW2GDvJ112vA            80   
514             2536            2536  1cGgVvEbuBlW2GDvJ112vA           115   
540             2632            2632  1cGgVvEbuBlW2GDvJ112vA            67   
560             2676            2676  FWRtx_h3plgIq-9pucg_9w            40   
590             2811            2811  AFF2vsQmRT4L22AvUsit-Q           156   
610             2923            2923  AFF2vsQmRT4L22AvUsit-Q            28   
615             3013            3013  MxiIRbKhCgT9Dz0hXg92vw           151   
637             3167            3167  CB8HrynUWR4Odnj-XTY-Ew           177   
648             3184            3184  CB8HrynUWR4Odnj-XTY-Ew             4   
654             3202            3202  CB8HrynUWR4Odnj-XTY-Ew           129   
655             3203            3203  CB8HrynUWR4Odnj-XTY-Ew            34   
699             3328            3328  CB8HrynUWR4Odnj-XTY-Ew            44   
824             3832            3832  oDBz4UnpaAVkBFGEAUaQPA           185   
836             3846            3846  oDBz4UnpaAVkBFGEAUaQPA          1040   
897             4047            4047  UNrAjQvmbszSL6SmV9FIyg           202   
964             4383            4383  L_tieGcFMQVSmk7XiA093A            11   
972             4405            4405  L_tieGcFMQVSmk7XiA093A            87   
988             4549            4549  4cIUCLqLuV2Y1ZlKfjjTPA            48   
1136            5238            5238  C16ogi6ASv-sQW3SGScmNQ           343   
1139            5256            5256  C16ogi6ASv-sQW3SGScmNQ            12   
1360            6072            6072  reWJsdKX1hzJwPCBj2Fcpg            29   
1408            6284            6284  1DtyA7pnc66hTkv64lKlzw             3   
1459            6600            6600  6mI2kt70hiOb0UaNYXfS8w            89   
...              ...             ...                     ...           ...   
168860        741963          741963  5Qxf1PZFuZ1tnO810pu28A            70   
168874        742115          742115  MqH1eJaXrP9X92AijQi3lw             3   
168877        742118          742118  MqH1eJaXrP9X92AijQi3lw           102   
168881        742158          742158  J-_Tb20y1PhzTbP0IlmMHg            20   
168883        742164          742164  J-_Tb20y1PhzTbP0IlmMHg           258   
168897        742341          742341  dLRmh34zinj1XZQzU4ENzQ             5   
168913        742402          742402  vtT5LzqjBjNymliYf4uEfw            74   
168914        742403          742403  vtT5LzqjBjNymliYf4uEfw             3   
169122        743404          743404  l0QlXA7tW9p2_glE2ziITw             7   
169158        743473          743473  grVfUvD9bvdDiK1UjlCo5w            84   
169244        743724          743724  37kk0IW6jL7ZlxZF6k2QBg             1   
169249        743736          743736  37kk0IW6jL7ZlxZF6k2QBg            38   
169250        743738          743738  37kk0IW6jL7ZlxZF6k2QBg           257   
169255        743766          743766  37kk0IW6jL7ZlxZF6k2QBg           185   
169303        743996          743996  Vu2C9npNSaHLYM7lvkKJJQ           151   
169383        744371          744371  7GSBz8XKGkX0f1XRJwBH_Q            56   
169400        744459          744459  hZJ_kOyj4xsaqb6lAzT_9w             5   
169404        744467          744467  hZJ_kOyj4xsaqb6lAzT_9w            69   
169422        744541          744541  EJmiKQKlWfY-0iVlya7FOQ           128   
169514        744798          

In [156]:
cur_df['review_text'][164]

'We went by for some brunch on a Sunday and had the pre set snack for $25. It came with a croissant cut in half, 2 chocolates, 2 halves of a candied orange, 4 small savoury cookies, 4 small sweet cookies and 3 small cubes of cheese along with blueberry jam. \xa0I had a tea and my wife had a coffee. It was really good and the place is quite nice and comfortable. To go: some flan and 3 Florentines The final bill was $56.27 and after tip $64.71I would go back again. If you can get past the price, the quality and service is excellent. Everything is actually imported from France so if that is important to you, this would be the place to go.'

In [297]:
len(target_df_index[0])

3613

In [204]:
# First find the original text
cur_df.loc[1790]['review_text']
cur_df.loc[1790]['review']


"['took', 'min', 'sitting', 'table', 'normal', 'busy', 'restaurant', 'server', 'came', 'ask', 'order', 'min', 'server', 'quite', 'good', 'cmon', 'great', 'ambiance', 'bailey', 'horchata', 'quite', 'nice', 'old', 'fashioned', 'nt', 'old', 'fashioned', 'bartender', 'mistake', 'gave', 'manhattan', 'instead', 'old', 'fashioned', 'made', 'decent', 'small', 'ice', 'cube', 'sacrilege', 'diluting', 'breakfast', 'burger', 'bad', 'shashuka', 'quite', 'quite', 'nice', 'overall', 'bad', 'experience', 'initial', 'hiccup', 'done']"

In [249]:
# Get the sentences of the orignal text
from nltk.tokenize import sent_tokenize
text = cur_df.loc[1790]['review_text']
sent_tokenize(text)

['It took 12 min after sitting down at the table in a normal not so busy restaurant before the server came through to ask for H2O or order.',
 '12 min.',
 'The server was quite good after but 12min!',
 "C'mon.",
 'Great ambiance.',
 "the Baileys Horchata quite nice, the Old Fashioned wasn't an old fashioned.",
 'Bartender mistake.',
 'Gave me a Manhattan instead.',
 'Old fashioned made again.',
 'Decent.',
 'But why the small ice cubes!!',
 'Sacrilege diluting it all.',
 'The breakfast burger was not bad but the Shashuka was quite quite nice.',
 'Overall.',
 'Not a bad experience once the initial hiccup was done.']

In [264]:
preprocess_sentence(sentences[0])

'took min sitting table normal busy restaurant server came ask order'

In [286]:
# Find the sentence contains the keyphrase
key_word = 'nice'
sentences = sent_tokenize(text)
# ind = np.where([key_word in sentence.lower() for sentence in sentences]) # we can do a preprocess here for each sentence
ind = np.where([key_word in preprocess_sentence(sentence) for sentence in sentences])
target_sentences = [preprocess_sentence(sentences[ind[0][i]]) for i in range(len(ind[0]))]
target_sentences

['bailey horchata quite nice old fashioned nt old fashioned',
 'breakfast burger bad shashuka quite quite nice']

In [289]:
# find relative positive or negative
sentence = target_sentences
sid = SentimentIntensityAnalyzer()
vader_scores = [sid.polarity_scores(sentence)['compound'] for sentence in sentence]
vader_scores
# ss = sid.polarity_scores(sentence)
# ss

[0.4754, -0.0332]

# Get the table ratio given keyword

In [90]:
from nltk.tokenize import sent_tokenize
def get_vader_scores_for_sentences_containing_the_keyword(key_word,cur_df,original_review = 'review_text',processed_review = 'conca_review'):
    # First find the reviews that contains the word 
    target_df_index = np.where(cur_df[processed_review].str.contains(key_word))[0]
    # for each review, get the vader scores 
    vader_scores = []
    for i in target_df_index:
        
        # For each review first find the original text
#         text = cur_df.loc[i][original_review]
        text = cur_df[original_review][i]
        
        # Get the sentences of the orignal text
        sentences = sent_tokenize(text)
        
        # Find the sentence containing the key word
        ind = np.where([key_word in preprocess_sentence(sentence) for sentence in sentences])
        target_sentences = [preprocess_sentence(sentences[ind[0][i]]) for i in range(len(ind[0]))]
        
        # find relative positive or negative vader scores
        sentence = target_sentences
        sid = SentimentIntensityAnalyzer()
        vader_score = [sid.polarity_scores(sentence)['compound'] for sentence in sentence]
        vader_scores.append(vader_score)
        
    return vader_scores

def find_dataframe_for_item(cur_df, ItemIndex, ItemIndex_col = 'ItemIndex'):
    """
    Return the dataframe that only contains the reviews 
    """
    new_df = cur_df.loc[np.where(cur_df[ItemIndex_col] == ItemIndex)]
    new_df = new_df.reset_index()
    return new_df

def count_pos_neg(vader_result, threshold = 0):
    """
    From the vader score lists, get the positive/negative list  
    """
    pos_count = 0
    neg_count = 0
    if len(vader_result) == 0:
        return [0,0]
    for i in range(len(vader_result)):
        for j in range(len(vader_result[i])):
            if vader_result[i][j] > threshold:
                pos_count += 1
            else:
                neg_count += 1
    return [pos_count,neg_count]

def get_aspect_ratio(cur_df, ItemIndex, aspect_keywords, ItemIndex_col = 'ItemIndex', threshold = 0, original_review = 'review_text',processed_review = 'conca_review'):
    target_df = find_dataframe_for_item(cur_df,ItemIndex)
    vader_scores = get_vader_scores_for_sentences_containing_the_keyword(aspect_keywords,target_df)
    ratio = count_pos_neg(vader_scores,threshold=threshold)
    return ratio

In [114]:
get_aspect_ratio(cur_df, 8010, 'food',
                ItemIndex_col = 'ItemIndex', threshold = 0, original_review = 'review_text',processed_review = 'conca_review')

[0, 1]

In [115]:
def get_category_ratio(cur_df, ItemIndex, keywords):
    res = [0, 0]
    for keyword in keywords:
        a,b = get_aspect_ratio(cur_df, ItemIndex, keyword,
                ItemIndex_col = 'ItemIndex', threshold = 0, original_review = 'review_text',processed_review = 'conca_review')
        res[0]+= a
        res[1]+= b
    return res

In [142]:
get_category_ratio(cur_df, 8517, location)

[15, 5]

In [160]:
get_category_ratio(cur_df, 8517, food_quality)

[207, 69]

In [164]:
get_category_ratio(cur_df, 8517, service)

[42, 25]

In [145]:
get_category_ratio(cur_df, 8517, price)

[54, 36]

In [146]:
get_category_ratio(cur_df, 8517, ambiance)

[4, 1]

In [158]:
get_category_ratio(cur_df, 8517, other)

[95, 50]

In [165]:
# food_quality = ['good dessert','try dessert','dessert','good texture','flavour texture', 'good meat','quality meat',]
# service = ['fast service','service excellent','friendly service', 'attentive service', 'excellent service','great service',
#           'amazing service', 'great customer service', 'fast service', 'good service', 'impressed service', 
#            'busy service', 'slow service', 'bad service', 'disappointed service', 'poor service', 'terrible service', 
#            'violating term service' ]
# price = ['good price', 'great price', 'regular price', 'reasonable price','decent price', 'cheap'
#          ,'high price','pricy', 'expensive']
# ambiance = ['good vibe','ambiance', ]
# location = []
# other = ['quick lunch',]
food_quality = ['taste','tasty','quality','food','dessert','texture','fresh', 'meat','vegetable','seafood','dish','delicious']
drink = ['coffee','tea','beer','drink']
service = ['service']
price = ['cheap','price','pricy','expensive']
ambiance = ['vibe','ambiance','atmosphere']
location = ['location','parking','street']
other = ['bathroom','washroom','table','place','experience']

## Draft

In [85]:
zero_df = find_dataframe_for_item(cur_df,8441)
vader_scores = get_vader_scores_for_sentences_containing_the_keyword('ambiance',zero_df)
count_pos_neg(vader_scores,threshold=0.05)

[1, 0]

In [81]:
zero_df = find_dataframe_for_item(cur_df,8441)
get_vader_scores_for_sentences_containing_the_keyword('vibe',zero_df)

[[0.8779]]

In [306]:
get_vader_scores_for_sentences_containing_the_keyword('ambiance',cur_df)

[[0.836],
 [0.4215],
 [0.8176],
 [0.5859],
 [0.975],
 [0.2023],
 [0.8807],
 [-0.5423],
 [0.0],
 [0.4404],
 [0.34],
 [0.0],
 [0.0],
 [0.2023],
 [0.7964],
 [0.7783],
 [0.5859],
 [0.6124],
 [0.6908],
 [0.4215],
 [0.8658],
 [0.6597],
 [0.7506],
 [0.8481],
 [0.7269],
 [0.2023],
 [0.765],
 [0.7351],
 [0.7402],
 [0.4215],
 [0.0],
 [0.9517],
 [0.5859],
 [0.765],
 [0.8225],
 [0.6705],
 [0.4201],
 [0.6249],
 [0.7579],
 [0.9062],
 [0.707],
 [0.8126],
 [0.6486],
 [0.4215],
 [0.8442],
 [0.9022],
 [0.8225],
 [0.0],
 [-0.1604],
 [0.4754],
 [0.4939],
 [0.0],
 [0.9413],
 [0.6369],
 [0.743],
 [0.9099, 0.6249],
 [0.7579],
 [0.8885],
 [0.8074],
 [-0.3182],
 [0.0],
 [0.3612],
 [0.9349],
 [-0.1779, 0.4767],
 [0.6249],
 [0.5859],
 [0.807],
 [0.4215],
 [0.9136],
 [0.3818],
 [-0.0516],
 [0.4215],
 [-0.4767],
 [0.8779],
 [0.7579],
 [0.0],
 [0.0],
 [0.6908],
 [0.0, 0.0],
 [0.6908],
 [0.9839],
 [0.0],
 [0.5994],
 [0.2732],
 [0.4404],
 [-0.2732],
 [0.7269],
 [0.6249, 0.0],
 [-0.0276],
 [0.836],
 [0.6249],
 [0.8442

In [120]:
neg_rating

['violating term service ',
 'terrible service ',
 'vietnamese coffee ',
 'friend star ',
 'disappointed place ',
 'mixed review ',
 'duck confit ',
 'delicious flavour ',
 'thin crust ',
 'nice crispy ',
 'little place ',
 'enjoyed dish ',
 'different place ',
 'service excellent ',
 'friendly place ',
 'pleasant surprise ',
 'coffee tea ',
 'decent size ',
 'paper bag ',
 'birthday party ',
 'good vibe ',
 'good texture ',
 'reservation advance ',
 'high chair ',
 'great recommendation ',
 'great choice ',
 'free parking ',
 'great option ',
 'enjoyed place ',
 'thing note ',
 'wait try ',
 'little gem ',
 'nt understand ',
 'overall great experience ',
 'greek food ',
 'place yelp ',
 'extensive menu ',
 'small shop ',
 'good well ',
 'bad review ',
 'tai fung ',
 'date night ',
 'poor service ',
 'wrong order ',
 'downtown core ',
 'smile face ',
 'hot summer day ',
 'creme brulee ',
 'wine list ',
 'bad day ']

In [119]:
pos_rating

['mixed review ',
 'cute place ',
 'small shop ',
 'extensive menu ',
 'place yelp ',
 'greek food ',
 'date night ',
 'hot summer day ',
 'wine list ',
 'smile face ',
 'good meat ',
 'enjoyed experience ',
 'enjoyed meal ',
 'creme brulee ',
 'small plaza ',
 'attentive food ',
 'overall great experience ',
 'egg waffle ',
 'bbq sauce ',
 'family style ',
 'much fun ',
 'tai fung ',
 'dinner menu ',
 'wait return ',
 'earl grey ',
 'reservation place ',
 'good care ',
 'delicious service ',
 'great spot ',
 'huge portion ',
 'good well ',
 'order next time ',
 'little gem ',
 'birthday party ',
 'friend star ',
 'delicious flavour ',
 'duck confit ',
 'different place ',
 'enjoyed dish ',
 'little place ',
 'vietnamese coffee ',
 'wait try ',
 'thin crust ',
 'service excellent ',
 'decent size ',
 'coffee tea ',
 'good vibe ',
 'nice crispy ',
 'great choice ',
 'thing note ']